In [1]:
import os
os.getcwd() 

'/root/notebooks'

In [4]:
import cPickle, string, numpy, getopt, sys, random, time, re, pprint
import wikirandom
#get_random_wikipedia_articles(n)
import onlineldavb
batchsize = 64
# The total number of documents in Wikipedia
D = 3.3e6
# The number of topics
K = 100
documentstoanalyze = 200

In [5]:
# Our vocabulary
vocab = file('./dictnostops.txt').readlines()
W = len(vocab)

# Initialize the algorithm with alpha=1/K, eta=1/K, tau_0=1024, kappa=0.7
olda = onlineldavb.OnlineLDA(vocab, K, D, 1./K, 1./K, 1024., 0.7)
# Run until we've seen D documents. (Feel free to interrupt *much*
# sooner than this.)
for iteration in range(0, documentstoanalyze):
    # Download some articles
    (docset, articlenames) = \
    wikirandom.get_random_wikipedia_articles(batchsize)
    # Give them to online LDA
    (gamma, bound) = olda.update_lambda(docset)
    # Compute an estimate of held-out perplexity
    (wordids, wordcts) = onlineldavb.parse_doc_list(docset, olda._vocab)
    perwordbound = bound * len(docset) / (D * sum(map(sum, wordcts)))
    print '%d:  rho_t = %f,  held-out perplexity estimate = %f' % \
    (iteration, olda._rhot, numpy.exp(-perwordbound))


downloaded 0/64 articles...
downloaded Trametinib. parsing...
downloaded Poplar_Grove,_Salt_Lake_City. parsing...
downloaded Macrorhineura. parsing...
downloaded 2009_Texas_Longhorns_football_team. parsing...
downloaded Saphenista_onychina. parsing...
downloaded Rollinia_occidentalis. parsing...
downloaded Natalya_Turkalo. parsing...
downloaded Pulavankadu. parsing...
downloaded 8/64 articles...
downloaded Division_of_Canning. parsing...
downloaded Ch%C3%ADa,_Cundinamarca. parsing...
downloaded Vorbunker. parsing...
downloaded Lancer_dragonet. parsing...
downloaded Gare_de_Saint-L%C3%B4. parsing...
downloaded McFadyen. parsing...
downloaded Aurora_Public_Schools. parsing...
downloaded Cultural_Summer_of_Zvornik. parsing...
downloaded 16/64 articles...
downloaded Newport_Free_Grammar_School. parsing...
downloaded Heidelberg_Project. parsing...
downloaded Ajoure. parsing...
downloaded Atopochilus_savorgnani. parsing...
downloaded Elisha_Gilbert_House. parsing...
downloaded Sogn_og_Fjorda

In [6]:
import json
articles = \
sc.textFile("s3n://stat-37601/wiki.json").map(lambda x: json.loads(x))

In [7]:
def parse(body):
    #choose the body betweetn <text> & </text>
    if body.find('<text') != -1: #if there's body
        start = body.index('<text')
        start = body.index('>',start)+1
        end = body.index('</text>') -1
        body = body[start:end]
        B = re.sub("<.*?>"," ", body)
        B = re.sub('\n',' ',B)
        B = "".join(c for c in B if c not in string.punctuation)
    else:
        B =''
        B = B.lower()

    return B

In [8]:
test=articles.map(lambda x : parse(x['body']))
test_list=test.collect()

In [12]:
test_list

[u'Other people redirectquotAirquot Jordanthe shoe and athletic wear companyAir Jordan Use mdy datesdateNovember 2012 ppsemiblpsmallyes ppmoveindef Infobox NBA biography image  Michael Jordanjpg caption  Michael Jordan in 2006 position  Shooting guard heightft  6heightin 6 weightlbs  216 nationality  American number  23 45 12ref labelNote1aa  birthdate  birth date and agemfyes1963217 birthplace  Brooklyn New York highschool  Emsley A Laney High SchoolEmsley A LaneyltbrgtWilmington North Carolina careerstart  1984 careerend  2003 draftyear  1984 draftround  1 draftpick  3 draftteam  Chicago Bulls college  North Carolina Tar Heels mens basketballNorth Carolina 1981\u20131984 years1 nbay1984start\u2013nbay1992end nbay1994end\u2013nbay1997end team1  Chicago Bulls years2 nbay2001start\u2013nbay2002end team2  Washington Wizards stat1label  Point basketballPoints stat1value  32292 301 ppg stat2label  Rebound basketballRebounds stat2value  6672 62 rpg stat3label  Assist basketballAssists stat3

In [13]:
olda_old=olda
olda = olda_old
(gamma, bound) = olda.update_lambda(test_list)

In [19]:
print len(gamma[0])
print len(gamma)

100
56


In [24]:
import numpy as np
for i in range(0,56):
    s=np.sum(gamma[i])
    gamma[i]=gamma[i]/s

In [25]:
numpy.sum(gamma[0])

0.99999999999999978

Here we use entropy to measure the similarity of two multinomial distributions.

In [27]:
def entropy(x):
    result = 0
    for i in x:
        result = result - i*np.log(i)
    return result

In [28]:
title = articles.map(lambda x: x['title'])
title_list=title.collect()

In [31]:
entros = []
for i in range(56):
    entros.append([entropy(gamma[i]),title_list[i],i])
entros = sorted(entros)
entros

[[1.8204286793599835, u'Japan_Post_Bank', 48],
 [2.25621642925165, u'Industrial_and_Commercial_Bank_of_China', 53],
 [2.4511564170403544, u'Aaron_Peirsol', 7],
 [2.4925205592352597, u'Mitsubishi_UFJ_Financial_Group', 55],
 [2.5361396010326804, u'Rebecca_Soni', 5],
 [2.5606223211507175, u'C_(programming_language)', 15],
 [2.5663684409845051, u'Natalie_Coughlin', 6],
 [2.5962670958648659, u'Beatles', 38],
 [2.7689294651415821, u'Kevin_Garnett\u200e', 3],
 [2.8101448117451557, u'Lionel_Messi', 11],
 [2.8464939213627027, u'R_(programming_language)', 19],
 [2.8721165104846076, u'Java_(programming_language)', 13],
 [2.879260866707039, u'Michael_Phelps', 4],
 [2.8894115038459551, u'Python_(programming_language)', 12],
 [2.910052306316854, u'Bank_of_America', 49],
 [2.9355869546820146, u'JavaScript', 18],
 [2.936391605067906, u'C_Sharp_(programming_language)', 16],
 [2.9456835364841911, u'Haskell_(programming_language)', 20],
 [2.9467919746285358, u'ING_Group', 52],
 [2.9592851673241167, u'The

In [63]:
t=0.01
s=1
sim_list=[]

for i in range(0,55):
    for j in range(s,56):
        if (entros[j][0]-entros[i][0])>=t:
            break
    s=j
    for k in range(i+1,s):
        sim_list.append((i,k))

Similar pairs are:


In [64]:
sim_list

[(5, 6),
 (11, 12),
 (15, 16),
 (16, 17),
 (17, 18),
 (23, 24),
 (25, 26),
 (27, 28),
 (28, 29),
 (29, 30),
 (30, 31),
 (31, 32),
 (32, 33),
 (33, 34),
 (34, 35),
 (38, 39),
 (44, 45),
 (44, 46),
 (44, 47),
 (45, 46),
 (45, 47),
 (46, 47)]

In [65]:
print "Similar pairs are:\n"
for x in sim_list:
    print 'articles', entros[x[0]][1],'and',entros[x[1]][1]

Similar pairs are:

articles C_(programming_language) and Natalie_Coughlin
articles Java_(programming_language) and Michael_Phelps
articles JavaScript and C_Sharp_(programming_language)
articles C_Sharp_(programming_language) and Haskell_(programming_language)
articles Haskell_(programming_language) and ING_Group
articles Ian_Thorpe and Oasis_(band)
articles Citigroup and Deutsche_Bank
articles Coldplay and Perl
articles Perl and Nirvana_(band)
articles Nirvana_(band) and Barclays
articles Barclays and JPMorgan_Chase
articles JPMorgan_Chase and Kobe_Bryant
articles Kobe_Bryant and LeBron_James
articles LeBron_James and AC/DC
articles AC/DC and Queen_(band)
articles Metallica and Diego_Maradona
articles United_States and Iran
articles United_States and China
articles United_States and Germany
articles Iran and China
articles Iran and Germany
articles China and Germany
